In [1]:
import numpy as np
import scipy
import scipy.stats
import pandas as pd
import astropy.units as u
import sunpy.map
import sunpy.visualization.colormaps as cm
import sunpy.data.sample
import reproject
import cv2
from sklearn.cluster import KMeans
from PIL import Image
from copy import copy
import datetime

import cv2

import matplotlib.pyplot as plt
import matplotlib.colors as colors
import seaborn as sns
import seaborn_image as isns
sns.set_style("darkgrid")

import os

import glob
import random

import utils

%matplotlib inline

In [2]:
hmiM_dir = "/mnt/disk2/downloads/hmi/hmi/"
hmiM_files = os.listdir(hmiM_dir)
hmiM_date_format = "hmi_m_45s_%Y_%m_%d_%H_%M_%S_tai_magnetogram.fits"
hmiM_dates = [datetime.datetime.strptime(i, hmiM_date_format) for i in hmiM_files]

aia193_dir = "data/aia_193A/"
aia193_files = os.listdir(aia193_dir)
aia193_date_format = "%Y-%m-%dT%H-%M-%S.fits"
aia193_dates = [datetime.datetime.strptime(i, aia193_date_format) for i in aia193_files]

aia211_dir = "data/aia_211A/"
aia211_files = os.listdir(aia211_dir)
aia211_date_format = "%Y-%m-%dT%H-%M-%S.fits"
aia211_dates = [datetime.datetime.strptime(i, aia211_date_format) for i in aia211_files]

## We take as a reference AIA193A and project the rest to it

In [3]:
corrupt_idx = [8197, 10021, 20118, 21086, 22198, 23608]
bad_idx = [998, 2790, 2843, 3715, 4203, 4429]

for aia193_idx, aia193_ref_file in enumerate(aia193_files):
    new_file_name = aia193_ref_file.replace('.fits', '.npy')

    if os.path.exists(f"data/composite_data/{new_file_name}"):
        print(f"file \"data/composite_data/{new_file_name}\" already exists")
        continue
    
    hmiM_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in hmiM_dates]
    aia211_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in aia211_dates]

    if max(min(hmiM_date_dist), min(aia211_date_dist)) < datetime.timedelta(hours=2) and aia193_idx not in corrupt_idx:
        print(aia193_idx)
        hmiM_idx = hmiM_date_dist.index(min(hmiM_date_dist))
        aia211_idx = aia211_date_dist.index(min(aia211_date_dist))


        aia193_map = sunpy.map.Map("data/aia_193A/" + aia193_ref_file)
        aia211_map = sunpy.map.Map("data/aia_211A/" + aia211_files[aia211_idx])
        hmiM_map = sunpy.map.Map("/mnt/disk2/downloads/hmi/hmi/" + hmiM_files[hmiM_idx])
        

        new_hmiM_map = hmiM_map.reproject_to(aia193_map.wcs)
        new_aia211_map = aia211_map.reproject_to(aia193_map.wcs)

        polar_aia193 = utils.map_to_polar(aia193_map)
        polar_aia211 = utils.map_to_polar(new_aia211_map)
        polar_hmiM = utils.map_to_polar(new_hmiM_map)

        composite_data = np.stack([polar_aia193, polar_aia211, polar_hmiM], axis=2)
        
        np.save(f"data/composite_data/{new_file_name}", composite_data)
        print(f"Saved tensor of size {composite_data.shape} to \"data/composite_data/{new_file_name}\"")

file "data/composite_data/2019-11-28T04-53-27.npy" already exists
file "data/composite_data/2019-10-31T05-22-26.npy" already exists
file "data/composite_data/2016-02-01T03-34-35.npy" already exists
file "data/composite_data/2018-11-18T08-45-01.npy" already exists
file "data/composite_data/2015-06-21T05-47-23.npy" already exists
file "data/composite_data/2015-11-28T04-43-04.npy" already exists
file "data/composite_data/2016-04-18T03-41-02.npy" already exists
file "data/composite_data/2019-11-15T11-52-18.npy" already exists
file "data/composite_data/2012-12-06T22-11-00.npy" already exists
file "data/composite_data/2017-05-11T04-41-28.npy" already exists
file "data/composite_data/2013-10-06T05-14-47.npy" already exists
file "data/composite_data/2019-04-01T09-32-08.npy" already exists
file "data/composite_data/2015-02-08T09-15-00.npy" already exists
file "data/composite_data/2018-08-13T06-41-34.npy" already exists
file "data/composite_data/2017-06-29T04-48-44.npy" already exists
file "data

/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <= max_func(output_image))
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <

Saved tensor of size (100, 360, 3) to "data/composite_data/2016-07-24T07-57-31.npy"
15452
Saved tensor of size (100, 360, 3) to "data/composite_data/2017-04-20T01-30-13.npy"
15453
Saved tensor of size (100, 360, 3) to "data/composite_data/2013-07-23T12-55-13.npy"
15454
Saved tensor of size (100, 360, 3) to "data/composite_data/2018-09-15T06-43-12.npy"
15455
Saved tensor of size (100, 360, 3) to "data/composite_data/2014-11-07T03-58-22.npy"
15456
Saved tensor of size (100, 360, 3) to "data/composite_data/2013-12-17T05-03-55.npy"
15457
Saved tensor of size (100, 360, 3) to "data/composite_data/2014-03-25T06-54-54.npy"
15458
Saved tensor of size (100, 360, 3) to "data/composite_data/2013-09-13T06-18-11.npy"
15459
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-02-16T00-52-08.npy"
15460
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-12-22T07-26-53.npy"
15461
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-07-07T01-30-14.npy"
15462
Saved tens

/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <= max_func(output_image))
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <

Saved tensor of size (100, 360, 3) to "data/composite_data/2013-07-21T09-40-46.npy"
15551
Saved tensor of size (100, 360, 3) to "data/composite_data/2015-06-28T07-01-49.npy"
15552
Saved tensor of size (100, 360, 3) to "data/composite_data/2015-07-22T02-33-46.npy"
15553
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-09-05T09-08-13.npy"
15554
Saved tensor of size (100, 360, 3) to "data/composite_data/2012-10-24T19-04-17.npy"
15555
Saved tensor of size (100, 360, 3) to "data/composite_data/2017-01-26T03-32-10.npy"
15556
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-05-14T02-49-05.npy"
15557
Saved tensor of size (100, 360, 3) to "data/composite_data/2015-06-30T01-30-04.npy"
15558
Saved tensor of size (100, 360, 3) to "data/composite_data/2014-09-28T06-58-23.npy"
15559
Saved tensor of size (100, 360, 3) to "data/composite_data/2012-10-16T21-21-32.npy"
15560
Saved tensor of size (100, 360, 3) to "data/composite_data/2020-05-23T01-30-04.npy"
15561
Saved tens

...

Saved tensor of size (100, 360, 3) to "data/composite_data/2013-01-20T08-25-47.npy"
24408
Saved tensor of size (100, 360, 3) to "data/composite_data/2020-06-15T08-01-35.npy"
24409
Saved tensor of size (100, 360, 3) to "data/composite_data/2017-07-24T03-35-12.npy"
24410
Saved tensor of size (100, 360, 3) to "data/composite_data/2012-10-22T04-08-05.npy"
24411
Saved tensor of size (100, 360, 3) to "data/composite_data/2018-09-12T09-17-19.npy"
24412
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-08-25T08-43-39.npy"
24413
Saved tensor of size (100, 360, 3) to "data/composite_data/2015-06-12T02-36-01.npy"
24414
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-01-20T02-30-08.npy"
24415
Saved tensor of size (100, 360, 3) to "data/composite_data/2017-11-25T10-02-23.npy"
24416
Saved tensor of size (100, 360, 3) to "data/composite_data/2020-02-05T10-40-45.npy"
24417
Saved tensor of size (100, 360, 3) to "data/composite_data/2020-03-19T07-04-48.npy"
24418
Saved tens

/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <= max_func(output_image))
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <

Saved tensor of size (100, 360, 3) to "data/composite_data/2014-04-06T06-48-29.npy"
24986
Saved tensor of size (100, 360, 3) to "data/composite_data/2015-12-09T10-07-46.npy"
24987
Saved tensor of size (100, 360, 3) to "data/composite_data/2018-05-02T05-20-31.npy"
24988
Saved tensor of size (100, 360, 3) to "data/composite_data/2020-06-18T02-35-52.npy"
24989
Saved tensor of size (100, 360, 3) to "data/composite_data/2012-10-18T13-58-16.npy"
24990
Saved tensor of size (100, 360, 3) to "data/composite_data/2014-04-30T07-19-38.npy"
24991
Saved tensor of size (100, 360, 3) to "data/composite_data/2013-02-16T07-43-08.npy"
24992
Saved tensor of size (100, 360, 3) to "data/composite_data/2015-10-07T03-41-37.npy"
24993
Saved tensor of size (100, 360, 3) to "data/composite_data/2019-03-03T10-13-54.npy"
24994
Saved tensor of size (100, 360, 3) to "data/composite_data/2020-05-16T03-42-51.npy"
24995
Saved tensor of size (100, 360, 3) to "data/composite_data/2018-04-29T10-16-45.npy"
24996
Saved tens

/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <= max_func(output_image))
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:725: RuntimeWarning: All-NaN slice encountered
  min_val = min_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:729: RuntimeWarning: All-NaN slice encountered
  max_val = max_func(input_image)
/home/eugeniolr/.local/lib/python3.10/site-packages/skimage/transform/_warps.py:735: RuntimeWarning: All-NaN slice encountered
  and min_func(output_image) <= cval <

Saved tensor of size (100, 360, 3) to "data/composite_data/2012-12-07T19-31-39.npy"
25700
Saved tensor of size (100, 360, 3) to "data/composite_data/2013-06-07T06-06-39.npy"
25701
Saved tensor of size (100, 360, 3) to "data/composite_data/2014-10-12T06-57-59.npy"
25702
Saved tensor of size (100, 360, 3) to "data/composite_data/2014-01-08T06-13-59.npy"
25703
Saved tensor of size (100, 360, 3) to "data/composite_data/2012-10-18T13-22-15.npy"
25704
Saved tensor of size (100, 360, 3) to "data/composite_data/2016-04-04T07-58-18.npy"
25705
Saved tensor of size (100, 360, 3) to "data/composite_data/2017-01-05T04-37-43.npy"
25706
Saved tensor of size (100, 360, 3) to "data/composite_data/2018-01-11T02-30-06.npy"
25707
Saved tensor of size (100, 360, 3) to "data/composite_data/2016-01-17T05-53-14.npy"
25708
Saved tensor of size (100, 360, 3) to "data/composite_data/2013-09-19T09-09-05.npy"
25709
Saved tensor of size (100, 360, 3) to "data/composite_data/2012-12-08T02-25-11.npy"
25710
Saved tens

In [4]:
corrupt_idx = [8197, 10021, 20118, 21086, 22198, 23608]

for aia193_idx, aia193_ref_file in enumerate(aia193_files):
    new_file_name = aia193_ref_file.replace('.fits', '.npy')

    if os.path.exists(f"data/composite_data/{new_file_name}"):
        print(f"file \"data/composite_data/{new_file_name}\" already exists")
        continue
    
    hmiM_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in hmiM_dates]
    aia211_date_dist = [abs(aia193_dates[aia193_idx] - ref_date) for ref_date in aia211_dates]

    if max(min(hmiM_date_dist), min(aia211_date_dist)) < datetime.timedelta(hours=2) and aia193_idx not in corrupt_idx:
        print(aia193_idx)
        hmiM_idx = hmiM_date_dist.index(min(hmiM_date_dist))
        aia211_idx = aia211_date_dist.index(min(aia211_date_dist))


        aia193_map = sunpy.map.Map("data/aia_193A/" + aia193_ref_file)
        aia211_map = sunpy.map.Map("data/aia_211A/" + aia211_files[aia211_idx])
        hmiM_map = sunpy.map.Map("/mnt/disk2/downloads/hmi/hmi/" + hmiM_files[hmiM_idx])
        

        new_hmiM_map = hmiM_map.reproject_to(aia193_map.wcs)
        new_aia211_map = aia211_map.reproject_to(aia193_map.wcs)

        # polar_aia193 = utils.map_to_polar(aia193_map)
        # polar_aia211 = utils.map_to_polar(new_aia211_map)
        # polar_hmiM = utils.map_to_polar(new_hmiM_map)

        composite_data = np.stack([aia193_map.data, new_aia211_map.data, new_hmiM_map.data], axis=2)
        
        np.save(f"data/composite_data/{new_file_name}", composite_data)
        print(f"Saved tensor of size {composite_data.shape} to \"data/composite_data/{new_file_name}\"")

file "data/composite_data/2019-11-28T04-53-27.npy" already exists
file "data/composite_data/2019-10-31T05-22-26.npy" already exists
file "data/composite_data/2016-02-01T03-34-35.npy" already exists
file "data/composite_data/2018-11-18T08-45-01.npy" already exists
file "data/composite_data/2015-06-21T05-47-23.npy" already exists
file "data/composite_data/2015-11-28T04-43-04.npy" already exists
file "data/composite_data/2016-04-18T03-41-02.npy" already exists
file "data/composite_data/2019-11-15T11-52-18.npy" already exists
file "data/composite_data/2012-12-06T22-11-00.npy" already exists
file "data/composite_data/2017-05-11T04-41-28.npy" already exists
file "data/composite_data/2013-10-06T05-14-47.npy" already exists
file "data/composite_data/2019-04-01T09-32-08.npy" already exists
file "data/composite_data/2015-02-08T09-15-00.npy" already exists
file "data/composite_data/2018-08-13T06-41-34.npy" already exists
file "data/composite_data/2017-06-29T04-48-44.npy" already exists
file "data